In [1]:
import re
import numpy as np
import pandas as pd
from pprint import pprint

# Gensim
import gensim
import gensim.corpora as corpora
from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel

# Plotting tools
import pyLDAvis
import pyLDAvis.gensim  # don't skip this
import matplotlib.pyplot as plt

# spacy for lemmatization
import spacy
import json
import warnings
import networkx as nx

warnings.filterwarnings("ignore",category=DeprecationWarning)

import nltk
nltk.download('stopwords')
nltk.download('words')

# NLTK Stop words
from nltk.corpus import stopwords
stop_words = stopwords.words('english')

from nltk.corpus import words
eng_words = words.words('en')

from langdetect import detect
# to enforce consistent results, check github langdetect readme
from langdetect import DetectorFactory
DetectorFactory.seed = 0


import os 

import csv

[nltk_data] Downloading package stopwords to
[nltk_data]     /home/siyanththan_v/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package words to
[nltk_data]     /home/siyanththan_v/nltk_data...
[nltk_data]   Package words is already up-to-date!


In [2]:
df = pd.read_csv('mount/TweetsOnUser.csv', lineterminator='\n', low_memory=False)
df.head()

id                                          TweetText  \
0   7515433917751296  Enjoy TSA Pat Down RT Hey everybody Thanksgivi...   
1  18960074751868928  Via RT Breaking News Assange signs book deal W...   
2  17700051287547904  state of heart soul your soul Birthing child m...   
3  21446749583314945                                       Sweet dreams   
4  18528789873041408  dramatic real Operation Clean-Up Now RT CRAP R...   

      userid        creationtimestamp  
0  194306325  2010-11-24 19:26:33 UTC  
1   86711072  2010-12-26 09:23:28 UTC  
2   39126647  2010-12-22 21:56:35 UTC  
3   23262180  2011-01-02 06:04:38 UTC  
4   71496690  2010-12-25 04:49:42 UTC

In [3]:
tweets = df.TweetText.values.tolist()
userIds = df.userid.values.tolist()
print("PLS")

PLS


In [4]:
dict = {}

for i in range(len(userIds)):
    if userIds[i] not in dict:
        dict[userIds[i]] = []
    for word in str(tweets[i]).split(" "):
        dict[userIds[i]].append(word)


In [10]:
data_final = list(dict.values())

In [11]:
# Create Dictionary
id2word = corpora.Dictionary(data_final)

# Create Corpus
# type(data_lemmatized)
# print (data_lemmatized)
texts = data_final

print(data_final[:1])

[['you!', 'I', 'love', 'xoxo', 'you!', 'I', 'proud', 'of', 'you', 'I', 'love', 'you', 'my', 'day', 'day.', 'After', 'After', 'all', 'all,', 'I', 'was', 'I', 'was', 'born', 'spread', 'I', 'am', 'love', "I'm", 'sadness', 'today', 'who', 'I', 'am', "I'm", 'thankful', 'everything', 'everyone', 'good', 'and', 'the', 'bad', 'happiness']]


In [13]:
# Term Document Frequency
corpus = [id2word.doc2bow(text) for text in texts]

# Human readable format of corpus (term-frequency)
print([[(id2word[id], freq) for id, freq in cp] for cp in corpus[:1]])

# Build LDA model
lda_model = gensim.models.ldamulticore.LdaMulticore(corpus=corpus,id2word=id2word,num_topics=30, passes=10, workers=3)

# Print the Keyword in the 10 topics
pprint(lda_model.print_topics())
doc_lda = lda_model[corpus]

# Compute Perplexity
print('\nPerplexity: ', lda_model.log_perplexity(corpus))  # a measure of how good the model is. lower the better.

[[('After', 2), ('I', 7), ("I'm", 2), ('all', 1), ('all,', 1), ('am', 2), ('and', 1), ('bad', 1), ('born', 1), ('day', 1), ('day.', 1), ('everyone', 1), ('everything', 1), ('good', 1), ('happiness', 1), ('love', 3), ('my', 1), ('of', 1), ('proud', 1), ('sadness', 1), ('spread', 1), ('thankful', 1), ('the', 1), ('today', 1), ('was', 2), ('who', 1), ('xoxo', 1), ('you', 2), ('you!', 2)]]
[(3,
  '0.019*"México" + 0.013*"Mexico" + 0.012*"Calderón" + 0.011*"Diego" + '
  '0.010*"Mty" + 0.009*"ALOHA" + 0.008*"Escobedo" + 0.008*"Marisela" + '
  '0.007*"PAN" + 0.007*"SURF"'),
 (4,
  '0.007*"Google" + 0.006*"Facebook" + 0.005*"You" + 0.005*"Twitter" + '
  '0.005*"Social" + 0.005*"iPhone" + 0.004*"iPad" + 0.004*"Apple" + '
  '0.004*"How" + 0.004*"Media"'),
 (28,
  '0.032*"cont" + 0.027*"RT" + 0.021*"di" + 0.014*"Indonesia" + 0.012*"yg" + '
  '0.012*"Jakarta" + 0.012*"dan" + 0.009*"yang" + 0.009*"ke" + 0.009*"ini"'),
 (9,
  '0.015*"free" + 0.012*"We" + 0.012*"today" + 0.011*"here" + 0.010*"Dec" + 

In [14]:
# def format_topics_sentences(ldamodel=lda_model, corpus=corpus, texts=data_lemmatized):
#     # Init output
#     sent_topics_df = pd.DataFrame()

#     # Get main topic in each document
#     for i, row in enumerate(ldamodel[corpus]):
#         print(row) 
#         topics = []
#         row = sorted(row, key=lambda x: (x[1]), reverse=True) 
#         for j, (topic_num, prop_topic) in enumerate(row):
#             if j in [0,1,2]: 
#                 topics.append(topic_num)
#         # Get the Dominant topic, Perc Contribution and Keywords for each document
#         for j, (topic_num, prop_topic) in enumerate(row):
# #             if j in [0,1,2]: #top 3 dominant topics
#             if j == 0:  # => dominant topic
#                 wp = ldamodel.show_topic(topic_num)
#                 topic_keywords = ", ".join([word for word, prop in wp])
#                 sent_topics_df = sent_topics_df.append(pd.Series([topics, round(prop_topic,4), topic_keywords]), ignore_index=True)
#             else:
#                 break
#     sent_topics_df.columns = ['Dominant_Topic', 'Perc_Contribution', 'Topic_Keywords']

def format_topics_sentences(ldamodel=lda_model, corpus=corpus, texts=data_final):
    # Init output
    sent_topics_df = pd.DataFrame()

    # Get main topic in each document
    for i, row in enumerate(ldamodel[corpus]):
        row = sorted(row, key=lambda x: (x[1]), reverse=True)
        # Get the Dominant topic, Perc Contribution and Keywords for each document
        for j, (topic_num, prop_topic) in enumerate(row):
            if j == 0:  # => dominant topic
                wp = ldamodel.show_topic(topic_num)
                topic_keywords = ", ".join([word for word, prop in wp])
                sent_topics_df = sent_topics_df.append(pd.Series([int(topic_num), round(prop_topic,4), topic_keywords]), ignore_index=True)
            else:
                break
    sent_topics_df.columns = ['Dominant_Topic', 'Perc_Contribution', 'Topic_Keywords']

    # Add original text to the end of the output
    contents = pd.Series(texts)
    sent_topics_df = pd.concat([sent_topics_df, contents], axis=1)
    return(sent_topics_df)


df_topic_sents_keywords = format_topics_sentences(ldamodel=lda_model, corpus=corpus, texts=data_final)

In [65]:
# Format
df_dominant_topic = df_topic_sents_keywords.reset_index()
df_dominant_topic.columns = ['Document_No', 'Dominant_Topic', 'Topic_Perc_Contrib', 'Keywords', 'Text']
#TER
# Show
df_dominant_topic.head(10)

Document_No  Dominant_Topic  Topic_Perc_Contrib  \
0            0            10.0              0.6732   
1            1            13.0              0.6472   
2            2            21.0              0.5281   
3            3            22.0              0.5404   
4            4            17.0              0.3131   
5            5            10.0              0.6154   
6            6            10.0              0.8063   
7            7            17.0              0.4683   
8            8            10.0              0.5733   
9            9             5.0              0.7123   

                                            Keywords  \
0  you, the, I, can, will, we, Christmas, one, do...   
1          I, you, RT, me, I'm, lol, my, up, can, it   
2  Obama, p2, GOP, tcot, tax, DADT, Senate, Palin...   
3  RT, Korea, US, WikiLeaks, China, BBC, will, So...   
4  Christmas, New, Video, the, TV, Music, The, of...   
5  you, the, I, can, will, we, Christmas, one, do...   
6  you, the, I, can, will, we, Christmas, one, do...   
7  Christmas, New, Video, the, TV, Music, The, of...   
8  you, the, I, can, will, we, Christmas, one, do...   
9       la, en, que, el, del, RT, un, para, por, con   

                                                Text  
0  [you!, I, love, xoxo, you!, I, proud, of, you,...  
1  [H., Jackson, Brown,, Jr, screwdriver, RT, Inf...  
2  [opinion, Sen, Cornyn, Repeal, Don’t, Ask,Don’...  
3  [Hope, stepson, hear, people, power, power, is...  
4  [Follow, Official, Goon, Gang, Djs, Week, 1, T...  
5  [charity:water, Paul, 1:1, 1, time, with, me, ...  
6  [Blue, Laws, Christmas, outlawed, Boston, you,...  
7  [Pink, Floyd, Wall, concert, last, night, pret...  
8  [Search, the, best, doctor, near, you, fb, wei...  
9  [Prototype, lanzó, su, 2011, e, Ivan, de, Pine...

In [72]:
userId_final = list(dict.keys())
userIdsCol = pd.DataFrame(userId_final)
userIdsCol.columns = ['User_Id']
userIdsCol.head(10)

User_Id
0  55836675
1  61560150
2  17563655
3  72613897
4  55050251
5        12
6        13
7  76082318
8  18874383
9  64749586

In [88]:
df_final = df_dominant_topic.merge(userIdsCol, left_index=True, right_index=True)
df_final.head(10)

Document_No  Dominant_Topic  Topic_Perc_Contrib  \
0            0            10.0              0.6732   
1            1            13.0              0.6472   
2            2            21.0              0.5281   
3            3            22.0              0.5404   
4            4            17.0              0.3131   
5            5            10.0              0.6154   
6            6            10.0              0.8063   
7            7            17.0              0.4683   
8            8            10.0              0.5733   
9            9             5.0              0.7123   

                                            Keywords  \
0  you, the, I, can, will, we, Christmas, one, do...   
1          I, you, RT, me, I'm, lol, my, up, can, it   
2  Obama, p2, GOP, tcot, tax, DADT, Senate, Palin...   
3  RT, Korea, US, WikiLeaks, China, BBC, will, So...   
4  Christmas, New, Video, the, TV, Music, The, of...   
5  you, the, I, can, will, we, Christmas, one, do...   
6  you, the, I, can, will, we, Christmas, one, do...   
7  Christmas, New, Video, the, TV, Music, The, of...   
8  you, the, I, can, will, we, Christmas, one, do...   
9       la, en, que, el, del, RT, un, para, por, con   

                                                Text   User_Id  
0  [you!, I, love, xoxo, you!, I, proud, of, you,...  55836675  
1  [H., Jackson, Brown,, Jr, screwdriver, RT, Inf...  61560150  
2  [opinion, Sen, Cornyn, Repeal, Don’t, Ask,Don’...  17563655  
3  [Hope, stepson, hear, people, power, power, is...  72613897  
4  [Follow, Official, Goon, Gang, Djs, Week, 1, T...  55050251  
5  [charity:water, Paul, 1:1, 1, time, with, me, ...        12  
6  [Blue, Laws, Christmas, outlawed, Boston, you,...        13  
7  [Pink, Floyd, Wall, concert, last, night, pret...  76082318  
8  [Search, the, best, doctor, near, you, fb, wei...  18874383  
9  [Prototype, lanzó, su, 2011, e, Ivan, de, Pine...  64749586

In [89]:
G=nx.Graph()
for row in df_final.itertuples(index=False):
    G.add_node(row.User_Id)
    if row.Dominant_Topic not in G:
        G.add_node(row.Dominant_Topic)
    G.add_edge(row.User_Id, row.Dominant_Topic, weight=row.Topic_Perc_Contrib)

In [ ]:
# Takes a while for graph to be displayed, cpu/ram increases so 
# instead of running this, printing out the nodes and edges is easier to
# inspect the graph

# nx.draw(G)
# plt.show()

In [92]:
for line in nx.generate_edgelist(G):
    print (line)

0.0 121430016 {'weight': 0.0333000011742115}
0.0 67293185 {'weight': 0.0333000011742115}
0.0 59187204 {'weight': 0.0333000011742115}
0.0 14106630 {'weight': 0.0333000011742115}
0.0 42254346 {'weight': 0.0333000011742115}
0.0 212000779 {'weight': 0.0333000011742115}
0.0 141135888 {'weight': 0.0333000011742115}
0.0 127512593 {'weight': 0.0333000011742115}
0.0 203747347 {'weight': 0.0333000011742115}
0.0 112693268 {'weight': 0.0333000011742115}
0.0 20955168 {'weight': 0.0333000011742115}
0.0 6291492 {'weight': 0.0333000011742115}
0.0 14733349 {'weight': 0.0333000011742115}
0.0 39010342 {'weight': 0.0333000011742115}
0.0 120897576 {'weight': 0.0333000011742115}
0.0 230203433 {'weight': 0.0333000011742115}
0.0 2606711 {'weight': 0.0333000011742115}
0.0 80580653 {'weight': 0.5164999961853027}
0.0 18210863 {'weight': 0.0333000011742115}
0.0 77602866 {'weight': 0.26649999618530273}
0.0 62918708 {'weight': 0.5023000240325928}
0.0 193527862 {'weight': 0.6025999784469604}
0.0 15582559 {'weight': 

1.0 86163833 {'weight': 0.8065000176429749}
1.0 15876673 {'weight': 0.8992999792098999}
1.0 18539075 {'weight': 0.5019999742507935}
1.0 31220292 {'weight': 0.9355000257492065}
1.0 24212918 {'weight': 0.4147999882698059}
1.0 92324422 {'weight': 0.607200026512146}
1.0 193356359 {'weight': 0.49639999866485596}
1.0 27247176 {'weight': 0.9896000027656555}
1.0 60570380 {'weight': 0.5164999961853027}
1.0 114542875 {'weight': 0.6765999794006348}
1.0 29213260 {'weight': 0.8065999746322632}
1.0 19086885 {'weight': 0.578000009059906}
1.0 40165966 {'weight': 0.7263000011444092}
1.0 117356415 {'weight': 0.9707000255584717}
1.0 97116752 {'weight': 0.8188999891281128}
1.0 9639352 {'weight': 0.5058000087738037}
1.0 66118226 {'weight': 0.7196999788284302}
1.0 17121875 {'weight': 0.8779000043869019}
1.0 19735124 {'weight': 0.8544999957084656}
1.0 45924949 {'weight': 0.4968999922275543}
1.0 32653911 {'weight': 0.6647999882698059}
1.0 117416536 {'weight': 0.36090001463890076}
1.0 14627653 {'weight': 0.552

1.0 17986014 {'weight': 0.5669000148773193}
1.0 8940342 {'weight': 0.4424000084400177}
1.0 23407415 {'weight': 0.7581999897956848}
1.0 19499832 {'weight': 0.32710000872612}
1.0 83356473 {'weight': 0.7484999895095825}
1.0 22457146 {'weight': 0.8515999913215637}
1.0 19401532 {'weight': 0.38530001044273376}
1.0 79964989 {'weight': 0.3614000082015991}
1.0 206998334 {'weight': 0.6021999716758728}
1.0 15727755 {'weight': 0.44519999623298645}
1.0 46500676 {'weight': 0.5910999774932861}
1.0 16747333 {'weight': 0.6620000004768372}
1.0 15371079 {'weight': 0.6829000115394592}
1.0 214224391 {'weight': 0.5065000057220459}
1.0 57854793 {'weight': 0.26429998874664307}
1.0 16321355 {'weight': 0.4876999855041504}
1.0 58846030 {'weight': 0.32739999890327454}
1.0 24067213 {'weight': 0.5342000126838684}
1.0 28805289 {'weight': 0.48010000586509705}
1.0 17836882 {'weight': 0.6917999982833862}
1.0 15838036 {'weight': 0.5867000222206116}
1.0 22547286 {'weight': 0.8252999782562256}
1.0 18205527 {'weight': 0.32

1.0 36091048 {'weight': 0.48179998993873596}
1.0 104917224 {'weight': 0.48539999127388}
1.0 8983922 {'weight': 0.39980000257492065}
1.0 25163124 {'weight': 0.7132999897003174}
1.0 37426217 {'weight': 0.5767999887466431}
1.0 109696374 {'weight': 0.6991999745368958}
1.0 121820535 {'weight': 0.7314000129699707}
1.0 30209400 {'weight': 0.4244000017642975}
1.0 54383993 {'weight': 0.8651999831199646}
1.0 29050531 {'weight': 0.5042999982833862}
1.0 31438204 {'weight': 0.5748999714851379}
1.0 117201130 {'weight': 0.28360000252723694}
1.0 82441598 {'weight': 0.38999998569488525}
1.0 20360943 {'weight': 0.5971999764442444}
1.0 98301312 {'weight': 0.659600019454956}
1.0 14399160 {'weight': 0.6783000230789185}
1.0 173970822 {'weight': 0.47540000081062317}
1.0 44397959 {'weight': 0.6736000180244446}
1.0 13265132 {'weight': 0.6251000165939331}
1.0 102913420 {'weight': 0.42820000648498535}
1.0 17911362 {'weight': 0.36000001430511475}
1.0 15742350 {'weight': 0.5903000235557556}
1.0 24172781 {'weight':

1.0 26574283 {'weight': 0.42320001125335693}
1.0 176225740 {'weight': 0.3587999939918518}
1.0 213888305 {'weight': 0.3937999904155731}
1.0 15023566 {'weight': 0.9688000082969666}
1.0 40033743 {'weight': 0.34470000863075256}
1.0 37813712 {'weight': 0.6996999979019165}
1.0 54287825 {'weight': 0.8924999833106995}
1.0 152378834 {'weight': 0.8618000149726868}
1.0 16535459 {'weight': 0.3495999872684479}
1.0 48973196 {'weight': 0.7088000178337097}
1.0 10238542 {'weight': 0.2937000095844269}
1.0 22748119 {'weight': 0.33379998803138733}
1.0 22633943 {'weight': 0.23119999468326569}
1.0 8207832 {'weight': 0.34619998931884766}
1.0 15474138 {'weight': 0.4153999984264374}
1.0 69443499 {'weight': 0.8349000215530396}
1.0 31447273 {'weight': 0.6958000063896179}
1.0 37666270 {'weight': 0.5533000230789185}
1.0 42950111 {'weight': 0.4724000096321106}
1.0 89112033 {'weight': 0.5920000076293945}
1.0 14745059 {'weight': 0.4957999885082245}
1.0 139116004 {'weight': 0.5356000065803528}
1.0 129741665 {'weight':

...

23.0 26387996 {'weight': 0.9251000285148621}
23.0 63292587 {'weight': 0.44519999623298645}
23.0 150828573 {'weight': 0.5257999897003174}
23.0 29082801 {'weight': 0.4551999866962433}
23.0 14427319 {'weight': 0.4706000089645386}
23.0 192898232 {'weight': 0.516700029373169}
23.0 121742523 {'weight': 0.4749000072479248}
23.0 22676668 {'weight': 0.3409000039100647}
23.0 134546623 {'weight': 0.516700029373169}
23.0 15221952 {'weight': 0.5008999705314636}
23.0 43192523 {'weight': 0.38940000534057617}
23.0 47858885 {'weight': 0.37630000710487366}
23.0 5653702 {'weight': 0.3467999994754791}
23.0 223986888 {'weight': 0.8359000086784363}
23.0 16868553 {'weight': 0.6711000204086304}
23.0 15500494 {'weight': 0.4875999987125397}
23.0 16606418 {'weight': 0.516700029373169}
23.0 69780691 {'weight': 0.6761000156402588}
23.0 64177364 {'weight': 0.5156000256538391}
23.0 146310357 {'weight': 0.23549999296665192}
23.0 213181655 {'weight': 0.516700029373169}
23.0 133432536 {'weight': 0.609499990940094}
23.0

23.0 17453563 {'weight': 0.5873000025749207}
23.0 87527932 {'weight': 0.5774000287055969}
23.0 205656573 {'weight': 0.2928999960422516}
23.0 156275200 {'weight': 0.516700029373169}
23.0 177623555 {'weight': 0.5759000182151794}
23.0 24908293 {'weight': 0.5116000175476074}
23.0 216961547 {'weight': 0.21170000731945038}
23.0 16732684 {'weight': 0.5648999810218811}
23.0 150135554 {'weight': 0.29899999499320984}
23.0 73661869 {'weight': 0.7602999806404114}
23.0 35852819 {'weight': 0.3319999873638153}
23.0 106566165 {'weight': 0.8597000241279602}
23.0 18649622 {'weight': 0.7009999752044678}
23.0 132223511 {'weight': 0.6658999919891357}
23.0 162959901 {'weight': 0.48910000920295715}
23.0 170357279 {'weight': 0.8061000108718872}
23.0 193163808 {'weight': 0.38989999890327454}
23.0 25260579 {'weight': 0.5785999894142151}
23.0 19264039 {'weight': 0.902999997138977}
23.0 183022121 {'weight': 0.40869998931884766}
23.0 172012075 {'weight': 0.516700029373169}
23.0 16175660 {'weight': 0.78079998493194

23.0 77184420 {'weight': 0.296999990940094}
23.0 111713702 {'weight': 0.44760000705718994}
23.0 15474087 {'weight': 0.753600001335144}
23.0 86760007 {'weight': 0.5012000203132629}
23.0 5438892 {'weight': 0.2842000126838684}
23.0 135439602 {'weight': 0.5509999990463257}
23.0 128581038 {'weight': 0.33649998903274536}
23.0 228507057 {'weight': 0.804099977016449}
23.0 147029427 {'weight': 0.516700029373169}
23.0 73080246 {'weight': 0.516700029373169}
23.0 18307657 {'weight': 0.7095000147819519}
23.0 41413004 {'weight': 0.5073000192642212}
23.0 25034172 {'weight': 0.838699996471405}
23.0 166892789 {'weight': 0.4429999887943268}
23.0 84236859 {'weight': 0.33219999074935913}
23.0 142392771 {'weight': 0.5767999887466431}
23.0 159923652 {'weight': 0.5982999801635742}
23.0 90987975 {'weight': 0.5216000080108643}
23.0 14135571 {'weight': 0.298799991607666}
23.0 146881993 {'weight': 0.7412999868392944}
23.0 52469201 {'weight': 0.8604999780654907}
23.0 122265042 {'weight': 0.3100999891757965}
23.0 

29.0 123774113 {'weight': 0.7213000059127808}
29.0 48551075 {'weight': 0.3691999912261963}
29.0 187262117 {'weight': 0.6207000017166138}
29.0 48395433 {'weight': 0.3944999873638153}
29.0 39939247 {'weight': 0.259799987077713}
29.0 204932273 {'weight': 0.43540000915527344}
29.0 143633590 {'weight': 0.257099986076355}
29.0 36828343 {'weight': 0.2935999929904938}
29.0 100646560 {'weight': 0.38989999890327454}
29.0 150140093 {'weight': 0.3246000111103058}
29.0 137002174 {'weight': 0.8618000149726868}
29.0 14998719 {'weight': 0.3443000018596649}
29.0 19578049 {'weight': 0.3546000123023987}
29.0 122793158 {'weight': 0.5418000221252441}
29.0 157459660 {'weight': 0.5163999795913696}
29.0 33873098 {'weight': 0.435699999332428}
29.0 212266188 {'weight': 0.5394999980926514}
29.0 128969933 {'weight': 0.3889999985694885}
29.0 91125965 {'weight': 0.5663999915122986}
29.0 59096272 {'weight': 0.44179999828338623}
29.0 111822035 {'weight': 0.4821999967098236}
29.0 208487639 {'weight': 0.758300006389617

132723


In [93]:
print(G.number_of_edges()) 
# gives 132723 edges, same as the number of user_ids

132723
